# Creating a Satellite Image of the Telescope Array Cosmic Ray Observatory
#### Author : Greg Furlich

In [1]:
## Loading Landsat 8 scence list ##
# Author : Greg Furlich
# Date : 2019-02-01

# Import Python Libraries #
import pandas as pd
import os, glob, wget
import matplotlib.pyplot as plt
from osgeo import gdal
import numpy as np

# plt.style.context('seaborn')

ImportError: libpoppler.so.71: cannot open shared object file: No such file or directory

### Load AWS Landsat 8 scene list csv

In [ ]:
#Import CSV File #
f = 'landsat_8_aws_scene_list'

df = pd.read_csv(f)

# Check DataFrame #
print(df.shape)
df.tail()

### Find Scences over Telescope Array

In [ ]:
## Find Entires over CLF Position ##
CLF_path = 38
CLF_row = 33

clf_df = df[df['path'] == CLF_path]
clf_df = clf_df[clf_df['row'] == CLF_row]

## Turn acquisition time into datetime ##
clf_df['acquisitionDate'] = pd.to_datetime(clf_df['acquisitionDate'])

## Cut on cloud cover ##
clf_df = clf_df[clf_df['cloudCover'] < 10 ]

## Sort by Most Recent Pass ##
clf_df = clf_df.sort_values('acquisitionDate',ascending=False)
clf_df.head()

### Create a Panda's DataFrame of the Landsat 8 Specs

In [ ]:
## Land Sat 8 Info Data Frame ## 

# Land Sat Bands #
bands = [ 'B{0}'.format(i) for i in range(1,10)]

#Band	Wavelength range (nanometers)	Spatial Resolution (m)	Spectral Width (nm)
#Band 1 - Coastal aerosol	430 - 450	30	2.0
#Band 2 - Blue	450 - 510	30	6.0
#Band 3 - Green	530 - 590	30	6.0
#Band 4 - Red	640 - 670	30	0.03
#Band 5 - Near Infrared (NIR)	850 - 880	30	3.0
#Band 6 - SWIR 1	1570 - 1650	30	8.0
#Band 7 - SWIR 2	2110 - 2290	30	18
#Band 8 - Panchromatic	500 - 680	15	18
#Band 9 - Cirrus	1360 - 1380	30	2.0
band_names = ['Band 1', 'Band 2', 'Band 3', 'Band 4', 'Band 5', 'Band 6', 'Band 7', 'Band 8', 'Band 9']
band_type = ['Coastal aerosol','Blue', 'Green', 'Red', 'NIR', 'SWIR 1', 'SWIR 2', 'Panchromatic', 'Cirrus']
band_wl_i =[430,450,530,640,850,1570,2110,500,1360]
band_wl_f = [450,510,590,670,880,2650,2290,680,1380]
band_sr = [30,30,30,30,30,30,30,15,30]
band_wl_w = [2,6,6,.03,3,8,18,18,2]

landsat = {'bands':bands, 'band_names': band_names, 'band_type': band_type, 'band_wl_i': band_wl_i, 'band_wl_f':band_wl_f, 'band_sr':band_sr, 'band_wl_w':band_wl_w}
landsat_df = pd.DataFrame(landsat)
landsat_df

### Download Land Sat 8 data from AWS

In [ ]:
## Download LandSat 8 TIFs from AWS ##
dir = '/GDF/TAResearch/TAmap/Landsat_imgs'

# Select Download info#
map_df = clf_df.head(1)
download_urls = str(map_df['download_url'].values[0])
entityId = str(map_df['entityId'].values[0])

# Make list of Images to download #
download_urls = download_urls.replace('/index.html','/{0}'.format(entityId))
download_urls = [ '{0}_{1}.TIF'.format(download_urls, band) for band in bands]

# Selected Scene
map_df

In [ ]:
## Download LandSat 8 TIFs from AWS ##

# Make Image Directory #
img_dir = dir + '/' + entityId 
if not os.path.exists(img_dir):
    os.makedirs(img_dir)

# Retrieve Images from AWS #
print('Saving to {0}'.format(img_dir))
for d in download_urls:
    print(img_dir+ d.split('/')[-1])
    if not os.path.isfile(img_dir+ '/'+d.split('/')[-1]):
        print('Retrieving {0}...'.format(d.split('/')[-1]))
        wget.download(d, out=img_dir)
    elif os.path.isfile(d.split('/')[-1]): print('{0} already exists...'.format(d.split('/')[-1]))

In [ ]:
## Loading Satelitte Image ##
from osgeo import gdal

# List Images Downloaded #
imgs = glob.glob(img_dir+'/*')
imgs.sort()

def norm(band):
    '''
    Normalize Spectrum Bands for Composite Image
    '''
    band_min, band_max = band.min(), band.max()
    return ((band - band_min)/(band_max - band_min))

# # Open Bands Using GDAL #
# b = gdal.Open(imgs[1])
# g = gdal.Open(imgs[2])
# r = gdal.Open(imgs[3])

# # call the norm function on each band as array converted to float
# b2 = norm(b.ReadAsArray().astype(np.float))
# b3 = norm(g.ReadAsArray().astype(np.float))
# b4 = norm(r.ReadAsArray().astype(np.float))

# # Create RGB Composite #
# rgb = np.dstack((b4,b3,b2))

# # Show Composite Image #
# plt.imshow(rgb)

# plt.savefig(dir+'/rgb_test.tif')

### Telescope Array Cosmic Ray Coordinates of Sites

In [ ]:
## TA Site Info ##

# See http://telescopearray.org/tawiki/index.php/CLF/FD_site_locations#Notes
site_name = ['Central Laser Facility','Black Rock Mesa','Long Ridge', 'Middle Drum']
site = ['CLF','BR','LR','MD']
site_color = ['blue', 'red', 'green', 'purple']
lat_dd = [39.29693,39.18830,39.20792,39.47282]
long_dd = [-112.90875,-112.71170,-113.12147,-112.99366]
alt_m = [1382,1404,1554,1600]
clf_x_km = [0,17.02811,-18.37754,-7.30807]
clf_y_km = [0,-12.0442,-9.86272,19.53612]
clf_z_km = [0,-.012095,.137922,.183828]
# FOV in CW from North #
fov_azm_i = [0, 242, 18, 102]
fov_azm_f = [0, 350, 125, 218]
# MD1
# 39 28 22.04278
# 112 59 39.15719
# LR1
# 39 12 28.32926
# 113 07 14.24482
# BR1
# 39 11 18.09744
# 112 42 45.44298
#  CLF1
# 39 17 48.44864 
# 112 54 31.81968
lat_deg = [39, 39, 39, 39]
long_deg = [112, 112, 113, 112]
lat_min = [17, 11, 12, 28]
long_min = [54, 42, 7, 59]
lat_sec = [48.44864, 18.09744, 28.32926, 22.04278]
long_sec = [31.81968, 45.44298, 14.24482, 39.15719]
lat = [ deg +  min/60 + sec/3600 for (deg, min, sec) in zip(lat_deg, lat_min, lat_sec)]
long = [ -1 * (deg +  min/60 + sec/3600) for (deg, min, sec) in zip(long_deg, long_min, long_sec)]

TA = {'Site Name': site_name,
      'Site': site,
      'Color': site_color,
      'Latitude': lat,
      'Longitude': long,
      'Altitude': alt_m,
      'X': clf_x_km,
      'Y': clf_y_km,
      'Z': clf_z_km,
      'FOVi': fov_azm_i,
      'FOVf': fov_azm_f,
      'Latitude DD': lat_dd,
      'Longitude DD': long_dd,}

## Convert Dictionary to Pandas DF ##
ta_df = pd.DataFrame(TA)
ta_df

### Function to center Raster on Point of Interest

In [ ]:
import rasterio

def centerPOI(max_lat, 
    min_lat, 
    max_lon, 
    min_lon, 
    raster, 
    poi_lat = ta_df[ta_df['Site'] == 'CLF']['Latitude'].values[0], 
    poi_lon = ta_df[ta_df['Site'] == 'CLF']['Longitude'].values[0], 
    pixels = 2000):
    '''
    Create a Window for the Rasters to Center on a Point of Interest (POI) within the Raster with given latitude and longitude of site.
    poi_lat = POI latitude in Degrees Decimal
    poi_lon = POI longitude in Degrees Decimal
    p = width of window in pixels. Each Pixel is 30m in width
    
    '''
    # Raster Longitude and Latitude Width #
    lon_range = max_lat - min_lat
    lat_range = max_lon - min_lon
#     print(max_lat, min_lat, lon_range)
#     print(max_lon, min_lon, lat_range)

    # Relative Position of POI #
    poi_x = (poi_lon - clf_df['min_lon'].values[0]) / lon_range
    poi_y = 1 - (poi_lat - clf_df['min_lat'].values[0]) / lat_range # Flipped y axis # 
    
    # Open Raster and Find Size #
    raster =  gdal.Open(raster)
    dx, dy = raster.RasterXSize, raster.RasterYSize

    # Find Position of POI in Raster #
    poi_x = poi_x * dx
    poi_y = poi_y * dy

    # Calculate Window for Focus on POI #
    # Window Corner #
    x_o, y_o = poi_x - .5 * pixels, poi_y - .5 * pixels
    # Window Width #
    d_x, d_y = pixels, pixels
    window = rasterio.windows.Window(x_o, y_o, d_x, d_y)
    
    return window

In [ ]:
# lon_range = clf_df['max_lon'].values[0] - clf_df['min_lon'].values[0]
# lat_range = clf_df['max_lat'].values[0] - clf_df['min_lat'].values[0]
# print(clf_df['max_lon'].values[0], clf_df['min_lon'].values[0], lon_range)
# print(clf_df['max_lat'].values[0], clf_df['min_lat'].values[0], lat_range)
# clf_lon, clf_lat = -112.90875, 39.29693
# md_lon, md_lat = -112.99366 , 39.47282
# lr_lon, lr_lat = -113.12147, 39.20792
# br_lon, br_lat = -112.71170, 39.18830
# clf_x = (br_lon - clf_df['min_lon'].values[0]) / lon_range
# clf_y = 1 - (br_lat - clf_df['min_lat'].values[0]) / lat_range

# print(clf_x,clf_y)

# raster =  gdal.Open(imgs[3])
# dx, dy = raster.RasterXSize, raster.RasterYSize
# print(dx, dy)
# pixel_range = 200
# clf_x = clf_x * dx
# clf_y = clf_y * dy
# print(clf_x,clf_y)

# x_o, y_o = clf_x - .5 * pixel_range, clf_y - .5 * pixel_range
# d_x,d_y = pixel_range, pixel_range
# window = rasterio.windows.Window(x_o, y_o, d_x, d_y)

# print(window)

### Load and Look at Landsat 8 Band Information

In [ ]:
## Load RGB Bands of Entry ##

# Create Window #
window = centerPOI(poi_lat = ta_df[ta_df['Site'] == 'CLF']['Latitude'].values[0], 
              poi_lon = ta_df[ta_df['Site'] == 'CLF']['Longitude'].values[0], 
              max_lat = map_df['max_lon'].values[0], 
              min_lat = map_df['min_lon'].values[0], 
              max_lon = map_df['max_lat'].values[0], 
              min_lon = map_df['min_lat'].values[0], 
              raster = imgs[3], 
              pixels = 2000)

# print(window)

# Load Bands #
r = rasterio.open(imgs[3]).read(1, window=window)
g = rasterio.open(imgs[2]).read(1, window=window)
b = rasterio.open(imgs[1]).read(1, window=window)
pan = rasterio.open(imgs[8]).read(1, window=window)

# Normalize Bands #
b2 = norm(b.astype(np.float))
b3 = norm(g.astype(np.float))
b4 = norm(r.astype(np.float))
b8 = norm(pan.astype(np.float))

# Create RGB Composite #
rgb = np.dstack((b4,b3,b2))

In [ ]:
# Create Histogram of RGB Spectrums #
plt.hist(b.ravel(), alpha=.2, color='blue',bins='auto',label='B')  # arguments are passed to np.histogram
plt.hist(g.ravel(), alpha=.2, color='green',bins='auto',label='G')
plt.hist(r.ravel(), alpha=.2, color='red',bins='auto',label='R')
plt.title('RGB Spectrum Histogram')
plt.legend()

In [ ]:
# Create Histogram of RGB Composite Spectrums #
plt.hist(rgb.ravel(), bins='auto',color='blue',label='RGB')
plt.title('RGB Composite Spectrum Histogram')
plt.legend()

In [ ]:
# Create Histogram of Panchromatic Spectrum #
plt.hist(pan.ravel(), bins='auto',label='RGB')
plt.title('Panchromatic Spectrum Histogram')
plt.legend()

### Plot Composite RGB Satellite Image

In [ ]:
## Plot Composite Satelite Image ##

plt.figure(figsize=(16,16))
plt.imshow(rgb)
plt.title('Delta Utah')
# plt.savefig(dir+'ta_array.png', dpi=600)
plt.savefig(dir+'delta.svg')

### Zoom in on Telescope Array Points of Interest

In [ ]:
## Create An Image of Each Site Zoomed in ##
fig = plt.figure(figsize=(16,16))
for (i, site, lat, lon) in zip(range(1,len(ta_df)+1),ta_df['Site'].values,ta_df['Latitude'].values,ta_df['Longitude'].values):
    plt.subplot(2,2,i)
    print(i, site, lat, lon)
    
    ## Finding Offset from recorded CLF lat and Long values to Center CLF ##
    lat_offset, lon_offset = -.015, -.017
    
    # Create Window #
    window = centerPOI(poi_lat = lat + lat_offset, 
              poi_lon = lon +  lon_offset, 
              max_lat = map_df['max_lon'].values[0], 
              min_lat = map_df['min_lon'].values[0], 
              max_lon = map_df['max_lat'].values[0], 
              min_lon = map_df['min_lat'].values[0], 
              raster = imgs[3], 
              pixels = 200)

    # Load Bands #
    r = rasterio.open(imgs[3]).read(1, window=window)
    g = rasterio.open(imgs[2]).read(1, window=window)
    b = rasterio.open(imgs[1]).read(1, window=window)

    # Normalize Bands #
    b2 = norm(b.astype(np.float))
    b3 = norm(g.astype(np.float))
    b4 = norm(r.astype(np.float))

    # Create RGB Composite #
    rgb = np.dstack((b4,b3,b2))

    # Plot Site #
    plt.imshow(rgb)
    plt.title('{0} : {1}, {2}'.format(site,lat,lon))
    
fig.suptitle('TA Sites with LandSat 8 Composite Images (30m Resolution)', fontsize=16)
plt.savefig(dir+'ta_sites.svg')

In [ ]:
## Add Sites to Map ##

## Load RGB Bands of Entry ##

# Create Window #
## Finding Offset from recorded CLF lat and Long values to Center CLF ##
lat_offset, lon_offset = -.015, -.017
    
    # Create Window #
window = centerPOI(poi_lat = ta_df[ta_df['Site'] == 'CLF']['Latitude'].values[0] + lat_offset, 
              poi_lon = ta_df[ta_df['Site'] == 'CLF']['Longitude'].values[0] + lon_offset, 
              max_lat = map_df['max_lon'].values[0], 
              min_lat = map_df['min_lon'].values[0], 
              max_lon = map_df['max_lat'].values[0], 
              min_lon = map_df['min_lat'].values[0], 
              raster = imgs[3], 
              pixels = 2000)

# print(window)

# Load Bands #
r = rasterio.open(imgs[3]).read(1, window=window)
g = rasterio.open(imgs[2]).read(1, window=window)
b = rasterio.open(imgs[1]).read(1, window=window)
pan = rasterio.open(imgs[8]).read(1, window=window)

# Normalize Bands #
b2 = norm(b.astype(np.float))
b3 = norm(g.astype(np.float))
b4 = norm(r.astype(np.float))
b8 = norm(pan.astype(np.float))

# Create RGB Composite #
rgb = np.dstack((b4,b3,b2))

plt.figure(figsize=(16,16))
plt.imshow(rgb)
plt.title('Telescope Array Cosmic Ray Observatory')
# plt.savefig(dir+'ta_array.png', dpi=600)
plt.savefig(dir+'ta_array.svg')

In [ ]:
## Create Field of View Arcs for site ##
def FOV_arc(r,ang_i,ang_f,xo,yo):
    d_ang = 100
    ang = np.linspace(ang_i,ang_f,d_ang)
    ring_x = r * np.sin(ang * np.pi / 180) + xo
    ring_y = r * np.cos(ang * np.pi / 180) + yo
    ring_x = np.concatenate(([xo],ring_x,[xo]))
    ring_y = np.concatenate(([yo],ring_y,[yo]))
    
    return ring_x, ring_y

In [ ]:
## Checking Haversine and Bearing Functions ##
import math

def haversine(longitude_1, latitude_1, longitude_2, latitude_2):
    """
    Calculate the great circle distance between two points p1 and p2
    on the earth (specified in decimal degrees)
    """
    
    # convert decimal degrees to radians #
    longitude_1, latitude_1, longitude_2, latitude_2 = map(math.radians, [longitude_1, latitude_1, longitude_2, latitude_2])

    # haversine formula #
    dlongitude = longitude_2 - longitude_1 
    dlatitude = latitude_2 - latitude_1 
    a = math.sin(dlatitude/2)**2 + math.cos(latitude_1) * math.cos(latitude_2) * math.sin(dlongitude/2)**2
    c = 2 * math.asin(math.sqrt(a)) 
    
    # Earth Radius in m from wikipedia #
    radius = [6378100, 6356800, 6378137, 6356752.3141, 6399593.6259, 
              6371008.7714, 6371007.1810, 6371000.7900, 6378137.0, 
              6356752.3142, 6399593.6258, 6371008.7714, 6371007.1809, 
              6371000.7900, 6378137.0, 6356752.314140, 6335439, 
              6384400, 6352800, 6371230]
    description = [
        'nominal \"zero tide\" equatorial',
        'nominal \"zero tide\" polar ',
        'equatorial radius',
        'semiminor axis (b)',
        'polar radius of curvature (c)',
        'mean radius (R1)',
        'radius of sphere of same surface (R2)',
        'radius of sphere of same volume (R3)',
        'WGS-84 ellipsoid, semi-major axis (a)',
        'WGS-84 ellipsoid, semi-minor axis (b)',
        'WGS-84 ellipsoid, polar radius of curvature (c)',
        'WGS-84 ellipsoid, Mean radius of semi-axes (R1)',
        'WGS-84 ellipsoid, Radius of Sphere of Equal Area (R2)',
        'WGS-84 ellipsoid, Radius of Sphere of Equal Volume (R3)',
        'GRS 80 semi-major axis (a)',
        'GRS 80 semi-minor axis (b)',
        'meridional radius of curvature at the equator',
        'Maximum (the summit of Chimborazo)',
        'Minimum (the floor of the Arctic Ocean)',
        'Average distance from center to surface'
    ]
    
    R_Earth = {'r': radius, 'description': description}
    R_Earth = pd.DataFrame(R_Earth)
    
    # Radius of the Earth in km #
    r = (R_Earth['r'][3] + ta_df['Altitude'][0])/ 1000
    #r = R_Earth['r'][3]/ 1000
    
    # Bearing Angle CW from North
    bearing = math.atan2(math.sin(longitude_2-longitude_1)*math.cos(latitude_2), math.cos(latitude_1)*math.sin(latitude_2)-math.sin(latitude_1)*math.cos(latitude_2)*math.cos(longitude_2-longitude_1))
 
    # Great Circle Distance #
    d = c * r
    
    # Convert Bearing Angle to degrees #
    # bearing = bearing * 180 / pi
        
    return d, bearing

def CLF_coord(longitude, latitude):
    '''
    Calculates the x and y components of distance between a a point with decimal degree longitude, latitude.
    CLF Coordinates :
    +x : East [m]
    +y : North [m]
    '''
    clf_longitude, clf_latitude = ta_df['Longitude'][0], ta_df['Latitude'][0]
    
    d, bearing = haversine(clf_longitude, clf_latitude, longitude, latitude)
        
    # Find the x and y component of the Distance #
    x = d * math.sin(bearing)
    y = d * math.cos(bearing)
    
    return x, y

### Import Surface Detector (SD) Locations

In [ ]:
## Import SD Positions ##
import re

# import .gpx file #
file_gps = '/GDF/TAResearch/TAmap//TASD.gpx' 

sd_lat = []
sd_lon = []
sd_id = []
sd_cmt = []
sd_alt = []
fgps = open(file_gps,'r')
for line in fgps.readlines():
#     print(line)
    # Find Lat and Lon #
    if re.findall('<wpt lat="([-0-9\.]+)" lon="([-0-9\.]+)">', line):
        latlon = re.findall('<wpt lat="([-0-9\.]+)" lon="([-0-9\.]+)">', line)
        sd_lat.append(float(latlon[0][0]))
        sd_lon.append(float(latlon[0][1])) 
    # Find ID #
    if re.findall('<name>([0-9]+)</name>', line):
        id = re.findall('<name>([0-9]+)</name>', line)
        sd_id.append(int(id[0]))
    # Find Comm Tower ##
    if re.findall('<cmt>(\D+)</cmt>', line):
        cmt = re.findall('<cmt>(\D+)</cmt>', line)
        sd_cmt.append(cmt[0])
    # Find Altitude #
    if re.findall('ele>([0-9\.]+)</ele>', line):
        alt = re.findall('<ele>([0-9\.]+)</ele>', line)
        sd_alt.append(float(alt[0]))

sd_x, sd_y = [], []
for (lat,lon) in zip(sd_lat,sd_lon):
    x, y = CLF_coord(lon, lat)
    sd_x.append(x)
    sd_y.append(y)
    
# sd_x, sd_y = [ x, y = CLF_coord(lon, lat) for (lat,lon) in zip(sd_lat,sd_lon)] 
sd_df = {'Latitude':sd_lat,'Longitude':sd_lon,'ID':sd_id,'altitude':sd_alt,'Communication Tower':sd_cmt,'X':sd_x,'Y':sd_y}

sd_df = pd.DataFrame(sd_df)
sd_df.head()

## Final Satellite Plot of Telescope Array Cosmic Ray Observatory

In [ ]:
## Finding Offset from recorded CLF lat and Long values to Center CLF ##
lat_offset, lon_offset = -.019, -.02

# Create Window #
window = centerPOI(poi_lat = ta_df[ta_df['Site'] == 'CLF']['Latitude'].values[0] + lat_offset, 
              poi_lon = ta_df[ta_df['Site'] == 'CLF']['Longitude'].values[0] + lon_offset, 
              max_lat = map_df['max_lon'].values[0], 
              min_lat = map_df['min_lon'].values[0], 
              max_lon = map_df['max_lat'].values[0], 
              min_lon = map_df['min_lat'].values[0], 
              raster = imgs[3], 
              pixels = 2000)

# Load Bands #
r = rasterio.open(imgs[3]).read(1, window=window)
g = rasterio.open(imgs[2]).read(1, window=window)
b = rasterio.open(imgs[1]).read(1, window=window)
pan = rasterio.open(imgs[8]).read(1, window=window)

# Normalize Bands #
b2 = norm(b.astype(np.float))
b3 = norm(g.astype(np.float))
b4 = norm(r.astype(np.float))
b8 = norm(pan.astype(np.float))

# Create RGB Composite #
rgb = np.dstack((b4,b3,b2))

# FOV Rings #
FOV_x, FOV_y = [], []
FOV_c = []   
for (ang_i, ang_f, xo, yo, color) in zip(ta_df['FOVi'].values,ta_df['FOVf'].values,ta_df['X'].values,ta_df['Y'].values,ta_df['Color'].values):
    r = 30
    x, y = FOV_arc(r, ang_i, ang_f, xo, yo)
    FOV_x.append(x)
    FOV_y.append(y)
    FOV_c.append(color)
    
## Composite Array Plot ##
fig = plt.figure(figsize=(16,16))

# Satellite Background #
ax=fig.add_subplot(111)
ax.imshow(rgb)
ax.tick_params(size=0)
ax.set_aspect('equal')
ax.set_yticklabels([])
ax.set_xticklabels([])

# FD Site Back Grounds #
clr_clf = '#EB4600'
clr_fd = '#065398'
clr_sd = '#4908A0'

ax2 = fig.add_subplot(111, frame_on=False)

# FD Sites #
# for (lat,lon,color,label) in zip(ta_df['Latitude DD'],ta_df['Longitude DD'],ta_df['Color'],ta_df['Site']):
#     x, y = CLF_coord(lon,lat)
for (x,y,label) in zip(ta_df['X'],ta_df['Y'],ta_df['Site']):
    if label == 'CLF' : ax2.scatter(x,y,marker='h', s=90, color=clr_clf)
    else : ax2.scatter(x,y,marker='^', s=90, color=clr_fd)
# SD Sites #
for (x,y) in zip(sd_df['X'],sd_df['Y']):
    ax2.scatter(x,y,marker='.', s=90, color=clr_sd)
# Label Sites #
for (x,y,text) in zip(ta_df['X'],ta_df['Y'],ta_df['Site']):
    #print (x,y,color,label)
    if text != 'CLF':
        if text == 'MD':
            ax2.text(x,y + 1.25,text, verticalalignment='center', horizontalalignment='center', fontsize=16, color='white')
        else :
            ax2.text(x,y - 1.25,text, verticalalignment='center', horizontalalignment='center', fontsize=16, color='white')
ax2.set_xlim([-30,30])
ax2.set_ylim([-30,30])
ax2.tick_params(size=0)
ax2.set_yticklabels([])
ax2.set_xticklabels([])
# Plot FOV #
for (x,y,c) in zip(FOV_x, FOV_y, FOV_c):
    if x[0] != 0 :
        alpha = .2
        ax2.fill(x,y,color=clr_fd,alpha=alpha)
        
# Stuff for Legend #
ax2.scatter(40,40,marker='^',color=clr_fd, label='FD Site')
ax2.scatter(40,40,marker='h',color=clr_clf, label='CLF Site')
ax2.scatter(40,40,marker='.',color=clr_sd, label='SD Site')

# Scale #
ax2.plot([-20,-10],[27,27],color='white')
ax2.text(-15, 28, '10 km', verticalalignment='center', horizontalalignment='center', color='white', fontsize=14)

# North Compass #
ax2.plot([-25,-25],[22,27],color='white')
ax2.text(-25, 28, 'North', verticalalignment='center', horizontalalignment='center', color='white', fontsize=14)
ax2.fill([-25,-25.5,-24.5],[27,26,26],color='white')

## Attribution ##
ax.text(0.98, 0.02, 'Greg Furlich\n USGS Landsat 8\n Telescope Array Cosmic Ray Observatory Satellite Map',
        verticalalignment='bottom', horizontalalignment='right',
        transform=ax.transAxes,
        weight='medium',
        color='white', fontsize=15)

# Plot Info #
# plt.title('Telescope Array Cosmic Ray Observatory')
# plt.xlabel('East [km]')
# plt.ylabel('North [km]')

leg =plt.legend(loc='upper right', bbox_to_anchor=(0.98, 0.98), prop={'size':16}, markerscale=2, framealpha = .2)
frame = leg.get_frame()
frame.set_color('white')
frame.set_linewidth(0)
for text in leg.get_texts():
    plt.setp(text, color = 'w')
    
ax2.set_aspect('equal')

# plt.show()
# plt.savefig('ta_map.svg', bbox_inches='tight', pad_inches=-.1)
plt.savefig('ta_map.png', bbox_inches='tight', pad_inches=0, dpi=400)